In [1]:
!pip install plotly==4.14.3  -i https://pypi.tuna.tsinghua.edu.cn/simple 

Looking in indexes: https://pypi.tuna.tsinghua.edu.cn/simple
  Created wheel for retrying: filename=retrying-1.3.3-py3-none-any.whl size=11429 sha256=9c95e0f2a060f6ba7544edb2211b4905f6282a0676d582592ec925d10ca97f26
  Stored in directory: c:\users\hp\appdata\local\pip\cache\wheels\a6\7c\dd\4c091a42e144b5556548677090b408fbe34511f5af804fe291
Successfully built retrying


In [2]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import seaborn as sns
import plotly.express as px
import plotly.graph_objs as go
import matplotlib.pyplot as plt
from scipy import stats
from collections import Counter
from plotly.offline import iplot

In [14]:
import os
data_dir=r'C:\Users\HP\Pictures\5005'

# Vaccine Brand Global Distribution

In [16]:
locations_df=pd.read_csv(os.path.join(data_dir,'locations.csv'))

In [17]:
vaccines = locations_df.vaccines.unique()
print(len(vaccines))
for v in vaccines:
    countries = locations_df.loc[locations_df.vaccines==v, 'location'].values
    print(f"Vaccines: {v}: \nCountries: {list(countries)}\n")

41
Vaccines: Oxford/AstraZeneca, Pfizer/BioNTech, Sinopharm/Beijing: 
Countries: ['Afghanistan', 'Maldives', 'Peru']

Vaccines: Oxford/AstraZeneca, Pfizer/BioNTech, Sinovac, Sputnik V: 
Countries: ['Albania', 'Bosnia and Herzegovina']

Vaccines: Sputnik V: 
Countries: ['Algeria', 'Armenia', 'Belarus', 'Guinea', 'Kazakhstan', 'Paraguay', 'Syria', 'Venezuela']

Vaccines: Oxford/AstraZeneca, Pfizer/BioNTech: 
Countries: ['Andorra', 'Australia', 'Cape Verde', 'Cayman Islands', 'Costa Rica', 'Isle of Man', 'Jersey', 'Oman', 'Panama', 'Saudi Arabia', 'Slovenia', 'South Korea', 'Sweden']

Vaccines: Oxford/AstraZeneca: 
Countries: ['Angola', 'Anguilla', 'Antigua and Barbuda', 'Bahamas', 'Bangladesh', 'Barbados', 'Belize', 'Bhutan', 'Botswana', 'Brunei', "Cote d'Ivoire", 'Democratic Republic of Congo', 'Dominica', 'Eswatini', 'Ethiopia', 'Falkland Islands', 'Fiji', 'French Polynesia', 'Gambia', 'Georgia', 'Ghana', 'Grenada', 'Guyana', 'Jamaica', 'Kosovo', 'Lesotho', 'Liberia', 'Madagascar', 'Ma

In [18]:
fig = px.choropleth(locations=locations_df['location'], 
                    locationmode="country names",
                    color=locations_df['vaccines'],
                    title="Countries using each vaccine (different colors for each vaccine)",
                   )
fig.update_layout({'legend_orientation':'h'})
fig.update_layout({'legend_title':'Vaccine scheme'})
fig.show()

# Vaccinations Progress Golbal

In [5]:
vaccinations_df=pd.read_csv(os.path.join(data_dir,'vaccinations.csv'))

In [6]:
vaccinations_df.head()

location iso_code        date  total_vaccinations  people_vaccinated  \
0  Afghanistan      AFG  2021-02-22                 0.0                0.0   
1  Afghanistan      AFG  2021-02-23                 NaN                NaN   
2  Afghanistan      AFG  2021-02-24                 NaN                NaN   
3  Afghanistan      AFG  2021-02-25                 NaN                NaN   
4  Afghanistan      AFG  2021-02-26                 NaN                NaN   

   people_fully_vaccinated  daily_vaccinations_raw  daily_vaccinations  \
0                      NaN                     NaN                 NaN   
1                      NaN                     NaN              1367.0   
2                      NaN                     NaN              1367.0   
3                      NaN                     NaN              1367.0   
4                      NaN                     NaN              1367.0   

   total_vaccinations_per_hundred  people_vaccinated_per_hundred  \
0                             0.0                            0.0   
1                             NaN                            NaN   
2                             NaN                            NaN   
3                             NaN                            NaN   
4                             NaN                            NaN   

   people_fully_vaccinated_per_hundred  daily_vaccinations_per_million  
0                                  NaN                             NaN  
1                                  NaN                            35.0  
2                                  NaN                            35.0  
3                                  NaN                            35.0  
4                                  NaN                            35.0

In [7]:
cols_data = []
total_data = []
df_by_country = []
for country in np.unique(vaccinations_df['location']):
    df_by_country.append(vaccinations_df[vaccinations_df['location']==country])

In [8]:
def last_item(col):
    total_vaccs = []
    for country in df_by_country:
        total_vaccs.append(np.array(country[col])[-1])
    data = dict(zip(np.unique(vaccinations_df['location']), total_vaccs))
    return data

In [10]:
def bars(data, x, y, title, figsize=(20, 12), rotation=75, size=8, width=None, height=None, colour=None):
    count = pd.DataFrame({x:data[x], y:data[y]}).sort_values(ascending=False, by=y)
    if not colour == None:
        c = count[colour]
    else:
        c = None
    fig = px.bar(count, x=x, y=y, title=title, width=width, height=height, color=c)
    fig.show()

In [12]:
def nulls(name, threshold, length):
    countries = np.array([])
    usable = 0
    for i in df_by_country:
        i = i.reset_index(drop=True)
        col = i[name]
        num_null = col.isnull().sum()
        col_len = len(col.index)
        usability = round(num_null/col_len*100, 2)<threshold
        if usability and col_len>length:
            usable += 1
            countries = np.append(countries, i['location'][0])
    return countries, name
def scatter(countries, col, threshold):
    i = 0
    fig = go.Figure()
    for country in countries:
        if list(vaccinations_df[vaccinations_df['location']==country][col])[-1]<threshold:
            if i % 2 == 0:
                i += 1
                continue
        i += 1
        df_temp = vaccinations_df[vaccinations_df['location']==country]
        trace = go.Scatter(x=df_temp['date'], y=df_temp[col], 
                           name=country,
                           mode='markers+lines')
        fig.add_trace(trace)
    fig.update_layout(legend_title=dict(text='Countries', font=dict(family="sans-serif",
                                         size=18)))
    fig.update_xaxes(title='date')
    fig.update_yaxes(title=col)
    fig.show()
for i in [['total_vaccinations', 10, 15, 1000000],
          ['total_vaccinations_per_hundred', 10, 15, 11],
          ['daily_vaccinations', 2.5, 20, 200000],
          ['daily_vaccinations_per_million', 2.05, 20, 0],
          ['people_fully_vaccinated', 60, 20, 500000],
          ['people_fully_vaccinated_per_hundred', 60, 20, 4]]:
    countries, title = nulls(i[0], i[1], i[2])
    scatter(countries, title, i[3])
